In [1]:
# Using plotly
import plotly.graph_objects as go
import numpy as np

Define data

In [2]:
import pandas as pd
data = pd.read_csv('stack_and_functions.csv')

def convert_to_int(value):
    try:
        if isinstance(value, str) and value.startswith('0x'):
            return int(value, 16)
        else:
            return int(value)
    except ValueError:
        return value 

data['start'] = data['start'].apply(convert_to_int)
data['end'] = data['end'].apply(convert_to_int)
data['size'] = data['end'] - data['start']

data.sort_values(by=['size'], inplace=True, ascending=False)
data.sort_values(by=['start'], inplace=True)

# Inverse the order of the data
data.reset_index(drop=True, inplace=True)

data['overlap'] = False

for i, row in data.iterrows():
    for j, row2 in data.iterrows():
        if i == j:
            continue
        if row['start'] <= row2['end'] and row['end'] > row2['start']:
            if row['end'] - row['start'] >= row2['end'] - row2['start']:
                continue
            data.at[i, 'overlap'] = True
            data.at[j, 'overlap'] = True
            data.at[i, 'overlap_with'] = j

data['overlap_with'] = data['overlap_with'].fillna(data.index.to_series())
data['overlap_with'] = data['overlap_with'].astype(float)

# Send warnings if sizes are negative
if (data['size'] < 0).any():
    print(f'Warning: Negative sizes detected at indices {data[data["size"] < 0].index}')

data

start        end                         name  order  comment  X0  LR  \
0           0     131072                      BootROM    NaN      NaN NaN NaN   
1         704        708                    _jump_bl1    NaN      NaN NaN NaN   
2       25824      25996                    _boot_usb    NaN      NaN NaN NaN   
3       75848      76008                     auth_bl1    NaN      NaN NaN NaN   
4    33660508   33689180         Tried debugger space    NaN      NaN NaN NaN   
5    33689440   33689448                 _boot_usb_ra    NaN      NaN NaN NaN   
6    33693696   33701888                          BL1    NaN      NaN NaN NaN   
7    33701888   33849344                         BL31    NaN      NaN NaN NaN   
8    33773056   33773064        TTBR0_EL3 address ptr    NaN      NaN NaN NaN   
9    33849344   34008336                          BL2    NaN      NaN NaN NaN   
10   33849344   33872624             BL2 empty space?    NaN      NaN NaN NaN   
11   33876736   33876736        BL2 copy start/source    NaN      NaN NaN NaN   
12   33984512   34009088                     Debugger    NaN      NaN NaN NaN   
13   34008336   34013184  End/Start peripheral space?    NaN      NaN NaN NaN   
14   34340864   34369536           Debugger relocated    NaN      NaN NaN NaN   
15   34340864   34340868           _frederic_dest_ptr    NaN      NaN NaN NaN   
16   34349056   34508048            BL2 load address?    NaN      NaN NaN NaN   
17   34371584   34373632              modem_interface    NaN      NaN NaN NaN   
18  287338512  287338512          memread/write space    NaN      NaN NaN NaN   
19  346816512  346836992                mali@14AC0000    NaN      NaN NaN NaN   

      size  overlap  overlap_with  
0   131072     True           0.0  
1        4     True           0.0  
2      172     True           0.0  
3      160     True           0.0  
4    28672    False           4.0  
5        8    False           5.0  
6     8192    False           6.0  
7   147456     True           7.0  
8        8     True           7.0  
9   158992     True           9.0  
10   23280     True           9.0  
11       0     True           9.0  
12   24576     True           9.0  
13    4848     True          12.0  
14   28672     True          16.0  
15       4     True          14.0  
16  158992     True          16.0  
17    2048     True          16.0  
18       0    False          18.0  
19   20480    False          19.0

Inherent stacked block diagram

In [3]:
import plotly.graph_objects as go
import random

tickpointers = []
vertical_len = len(data['overlap_with'].unique())
vertical_gap_percentage = 0.08
horizontal_gap = 0.1
labels = pd.DataFrame()

def random_color():
    return f'#{random.randint(0, 0xFFFFFF):06x}'

fig = go.Figure()

for i, d in data.iterrows():
    fillcolor = random_color()
    data.at[i, 'fillcolor'] = fillcolor
    
    x0=1
    x1=4

    if d['overlap'] == False:
        y0=d['overlap_with']
        y1=d['overlap_with']+1
    elif d['overlap'] == True:
        overlaps = data.loc[data['overlap_with'] == d['overlap_with']].shape[0]

        # Calculate relative size of the overlap
        overlap_sizes = data.loc[data['overlap_with'] == d['overlap_with']].iloc[1:]['size'].sum()

        if d['overlap_with'] == i:
            y0=i
            y1=overlaps+i
            if i != data.shape[0]+1:
                if d['end'] > data.iloc[i+1].start and d['end'] < data.iloc[i+1].end:
                    y1=overlaps+i-0.5
            x0=x0-horizontal_gap
            x1=x1+horizontal_gap
        else:
            y0=0.02+i
            y1=0.87+i
    else:
        print(f'Something went wrong with {d}. Skipping')
        continue

    fig.add_shape(
        type="rect",
        x0=x0,
        x1=x1,
        y0=y0+vertical_gap_percentage,
        y1=y1-vertical_gap_percentage,
        line=dict(width=2),
        fillcolor=fillcolor,
        opacity=0.5,
        layer="below",
    )

    # Add middle text
    fig.add_trace(go.Scatter
    (
        x=[(x0+x1)/2],
        y=[y0+0.5],
        text=d['name'],
        mode="text",
        textposition="middle center",
        name=d['name'],
        marker=dict(
            color=fillcolor,
        ),
    ))

    # Add top-left text with d['end']
    fig.add_trace(go.Scatter
    (
        x=[(x0+0.14+horizontal_gap)],
        y=[y1-0.16],
        text=hex(d['end']),
        mode="text",
        textposition="middle center",
        marker=dict(
            color=fillcolor,
        ),
        showlegend=False,
    ))

    # Add bottom-left text with d['end']
    fig.add_trace(go.Scatter
    (
        x=[(x0+0.14+horizontal_gap)],
        y=[y0+0.14],
        text=hex(d['start']),
        mode="text",
        textposition="middle center",
        marker=dict(
            color=fillcolor,
        ),
        showlegend=False,
    ))

fig.update_xaxes(
    range=[0, 5],
    tickvals=[0, 1, 2, 3, 4, 5],
)

start_values = data['start'].sort_values()
end_values = data['end'].sort_values()

labels = []

for i, d in data.iterrows():
    if i == 0:
        labels.append(f'{hex(start_values.iloc[i])}')
    elif i == len(data)-1:
        labels.append(f'{hex(end_values.iloc[i])}')
    else:
        labels.append(f'{hex(start_values.iloc[i])}<br>{hex(end_values.iloc[i-1])}')

tickpointers = [i for i in range(len(data))]

fig.update_yaxes(
    # tickvals=[i for i in range(len(data)+1)], 
    tickvals = tickpointers,
    # ticktext= labels,
    griddash="longdashdot",
    gridwidth=0,
    gridcolor="black",
    showgrid=False,
    showticklabels=True,
    autorange='reversed',
)

fig.update_xaxes(
    showgrid=False,
    showticklabels=False,
)

fig.update_layout(
    width=1200,
    height=1200,
    autosize=True,
    margin=dict(l=200, r=20, t=20, b=20),
    font=dict(
        size=18,
    ),
    # Legend being the name of the function
    legend_title_text="Function/Locations",
)

fig.show()

In [4]:
# Save to html
fig.write_html("../_static/stack_and_functions.html")

Layered blocks

In [5]:
import plotly.graph_objects as go
import random

tickpointers = []
vertical_len = len(data['overlap_with'].unique())
vertical_gap_percentage = 0.08
horizontal_gap = 0.1
labels = pd.DataFrame()

def random_color():
    return f'#{random.randint(0, 0xFFFFFF):06x}'

fig = go.Figure()

for i, d in data.iterrows():
    fillcolor = random_color()
    data.at[i, 'fillcolor'] = fillcolor
    
    x0=1
    x1=4

    if d['overlap'] == False:
        y0=d['overlap_with']
        y1=d['overlap_with']+1
    elif d['overlap'] == True:
        overlaps = data.loc[data['overlap_with'] == d['overlap_with']].shape[0]

        # Calculate relative size of the overlap
        overlap_sizes = data.loc[data['overlap_with'] == d['overlap_with']].iloc[1:]['size'].sum()

        if d['overlap_with'] == i:
            y0=i
            y1=overlaps+i
            if i != data.shape[0]+1:
                if d['end'] > data.iloc[i+1].start and d['end'] < data.iloc[i+1].end:
                    y1=overlaps+i-0.5
            x0=x0-horizontal_gap
            x1=x1+horizontal_gap
        else:
            y0=0.02+i
            y1=0.87+i
    else:
        print(f'Something went wrong with {d}. Skipping')
        continue

    fig.add_shape(
        type="rect",
        x0=x0,
        x1=x1,
        y0=y0+vertical_gap_percentage,
        y1=y1-vertical_gap_percentage,
        line=dict(width=2),
        fillcolor=fillcolor,
        opacity=0.5,
        layer="below",
    )

    # Add middle text
    fig.add_trace(go.Scatter
    (
        x=[(x0+x1)/2],
        y=[y0+0.5],
        text=d['name'],
        mode="text",
        textposition="middle center",
        name=d['name'],
        marker=dict(
            color=fillcolor,
        ),
    ))

    # Add top-left text with d['end']
    fig.add_trace(go.Scatter
    (
        x=[(x0+0.14+horizontal_gap)],
        y=[y1-0.16],
        text=hex(d['end']),
        mode="text",
        textposition="middle center",
        marker=dict(
            color=fillcolor,
        ),
        showlegend=False,
    ))

    # Add bottom-left text with d['end']
    fig.add_trace(go.Scatter
    (
        x=[(x0+0.14+horizontal_gap)],
        y=[y0+0.14],
        text=hex(d['start']),
        mode="text",
        textposition="middle center",
        marker=dict(
            color=fillcolor,
        ),
        showlegend=False,
    ))

fig.update_xaxes(
    range=[0, 5],
    tickvals=[0, 1, 2, 3, 4, 5],
)

start_values = data['start'].sort_values()
end_values = data['end'].sort_values()

labels = []

for i, d in data.iterrows():
    if i == 0:
        labels.append(f'{hex(start_values.iloc[i])}')
    elif i == len(data)-1:
        labels.append(f'{hex(end_values.iloc[i])}')
    else:
        labels.append(f'{hex(start_values.iloc[i])}<br>{hex(end_values.iloc[i-1])}')

tickpointers = [i for i in range(len(data))]

fig.update_yaxes(
    # tickvals=[i for i in range(len(data)+1)], 
    tickvals = tickpointers,
    # ticktext= labels,
    griddash="longdashdot",
    gridwidth=0,
    gridcolor="black",
    showgrid=False,
    showticklabels=True,
    autorange='reversed',
)

fig.update_xaxes(
    showgrid=False,
    showticklabels=False,
)

fig.update_layout(
    width=1200,
    height=1200,
    autosize=True,
    margin=dict(l=200, r=20, t=20, b=20),
    font=dict(
        size=18,
    ),
    # Legend being the name of the function
    legend_title_text="Function/Locations",
)

fig.show()